<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Read-DataFrame" data-toc-modified-id="Read-DataFrame-1">Read DataFrame</a></span></li><li><span><a href="#Folium" data-toc-modified-id="Folium-2">Folium</a></span><ul class="toc-item"><li><span><a href="#Using-Markers" data-toc-modified-id="Using-Markers-2.1">Using Markers</a></span></li><li><span><a href="#Using-Choropleth-Maps" data-toc-modified-id="Using-Choropleth-Maps-2.2">Using Choropleth Maps</a></span></li><li><span><a href="#Heatmaps" data-toc-modified-id="Heatmaps-2.3">Heatmaps</a></span></li></ul></li><li><span><a href="#Plotly" data-toc-modified-id="Plotly-3">Plotly</a></span><ul class="toc-item"><li><span><a href="#Scatter-Geo" data-toc-modified-id="Scatter-Geo-3.1">Scatter Geo</a></span></li><li><span><a href="#Density-Heatmap" data-toc-modified-id="Density-Heatmap-3.2">Density Heatmap</a></span></li><li><span><a href="#Animation" data-toc-modified-id="Animation-3.3">Animation</a></span></li></ul></li><li><span><a href="#Choropleth-Map" data-toc-modified-id="Choropleth-Map-4">Choropleth Map</a></span></li></ul></div>

## Read DataFrame

In [42]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
%matplotlib notebook

In [91]:
df = pd.read_csv('time_series_2019-ncov-Confirmed.csv')

df['Country/Region'].replace({'Mainland China':'China',
                              'US':'United States of America',
                              'UK':'United Kingdom'},
                             inplace=True)

In [92]:
df.head()

Province/State Country/Region      Lat      Long  1/22/20  1/23/20  1/24/20  \
0            NaN       Thailand  15.0000  101.0000        2        3        5   
1            NaN          Japan  36.0000  138.0000        2        1        2   
2            NaN      Singapore   1.2833  103.8333        0        1        3   
3            NaN          Nepal  28.1667   84.2500        0        0        0   
4            NaN       Malaysia   2.5000  112.5000        0        0        0   

   1/25/20  1/26/20  1/27/20  ...  3/10/20  3/11/20  3/12/20  3/13/20  \
0        7        8        8  ...       53       59       70       75   
1        2        4        4  ...      581      639      639      701   
2        3        4        5  ...      160      178      178      200   
3        1        1        1  ...        1        1        1        1   
4        3        4        4  ...      129      149      149      197   

   3/14/20  3/15/20  3/16/20  3/17/20  3/18/20  3/19/20  
0       82      114      147      177      212      272  
1      773      839      825      878      889      924  
2      212      226      243      266      313      345  
3        1        1        1        1        1        1  
4      238      428      566      673      790      900  

[5 rows x 62 columns]

In [45]:
# We will need the dates to be in one column

df1 = pd.melt(df, id_vars=['Country/Region', 'Province/State','Lat','Long'])
df1.head()

Country/Region Province/State      Lat      Long variable  value
0       Thailand            NaN  15.0000  101.0000  1/22/20      2
1          Japan            NaN  36.0000  138.0000  1/22/20      2
2      Singapore            NaN   1.2833  103.8333  1/22/20      0
3          Nepal            NaN  28.1667   84.2500  1/22/20      0
4       Malaysia            NaN   2.5000  112.5000  1/22/20      0

In [46]:
df1 = df1.rename(columns={'variable':'date','value':'cases'})

## Folium

In [47]:
import folium
from folium import plugins

### Using Markers


In [48]:
# Create Map Object m  in the middle of the world (coordinates 37 & -9)
m1 = folium.Map(location=[37,-9],zoom_start=2,
               tiles = "CartoDB positron")

In [49]:
# For loop for the circles
# Raduis will be the number of cases on 19th of March

for index, row in df.iterrows():    
    _radius = int(row['3/19/20']) 
    
    if np.isnan(_radius):
        _radius = 0
  
    lat, lon = row['Lat'], row['Long']  
    folium.CircleMarker(location = [lat,lon], 
                        radius = _radius/100000, 
                        color = '#E80018',
                        fill=True,
                        fill_opacity = 1).add_to(m1)

In [50]:
display(m1)

In [51]:
m1.save('folium-dots.html')

### Using Choropleth Maps

* **`folium.Choropleth()`**
    * **`geo_data`** the `.json` file that contains the coordinates
    * **`data`** df
    * **`columns`** list of: name of column that will match the `geo_data` file, and the name of the column that will take the data from
    * **`key_on`** location inside the `.json` file that will match the first argument of `columns`

the worlds' countries coordinates are uploaded using the json file `custom.geo.json`. The match to the dataframe will be using `columns` where the first argument is column name and the second is the data to capture from the df. `key_on` specifies which feature on the JSON file contains the data to match with the `Country/Region` chosen in `columns` attribute.

In [52]:
# Create a list of bins for the color bar

list(df['3/19/20'].quantile([0.6, 0.7, 0.9, 0.92, 0.94, 0.96, 0.98, 0.99, 1]))

[16.19999999999999,
 53.0,
 357.4000000000001,
 481.92000000000013,
 741.3999999999988,
 1177.2399999999993,
 2611.1399999999926,
 12339.16999999993,
 67800.0]

In [53]:
m2 = folium.Map(location=[37,-9],zoom_start=2,
               tiles = "CartoDB positron")

In [54]:
# Specifying my Bins
bins = list(df['3/19/20'].quantile([0, 0.3, 0.4, 0.5, 0.9, 0.95, 1]))

# Using Choropleth Maps
folium.Choropleth(geo_data="custom.geo.json",
             data=df, # my dataset
             columns=['Country/Region', '3/19/20'], # country/region is here for matching the geojson country names, '3/1/2020' is the column that changes the color of zipcode areas
             key_on='feature.properties.sovereignt', # this path contains name of country to match with data, this should match with our 'Country/Region' column
             fill_color='PuRd', 
             fill_opacity=1,
             line_opacity=1,
             legend_name='# of Cases',
             bins=bins,
            reset=True).add_to(m2)

display(m2)

In [55]:
m2.save('folium-choropleth.html')

### Heatmaps

NOTE: The heatmap is based on the location (`lat` and `long`) and not based on the numbers on each country. In other words, the heatmap is for how close points are, regardless of what value they hold

In [56]:
m3 = folium.Map(location=[37,-9],zoom_start=2)

In [57]:
from folium.plugins import HeatMap

heat_data = [[row['Lat'],row['Long']] for index, row in df.iterrows()]

# Plot it on the map
HeatMap(heat_data).add_to(m3)

In [58]:
m3

In [59]:
m3.save('folium-heat.html')

---------------------------

## Plotly

In [60]:
#!pip install plotly

In [61]:
import plotly.express as px

In [62]:
df1.head()

Country/Region Province/State      Lat      Long     date  cases
0       Thailand            NaN  15.0000  101.0000  1/22/20      2
1          Japan            NaN  36.0000  138.0000  1/22/20      2
2      Singapore            NaN   1.2833  103.8333  1/22/20      0
3          Nepal            NaN  28.1667   84.2500  1/22/20      0
4       Malaysia            NaN   2.5000  112.5000  1/22/20      0

### Scatter Geo

In [63]:
data = df1[df1.date=='3/19/20']
data = data[data.cases!=0]
data

Country/Region Province/State      Lat      Long     date  cases
26676        Thailand            NaN  15.0000  101.0000  3/19/20    272
26677           Japan            NaN  36.0000  138.0000  3/19/20    924
26678       Singapore            NaN   1.2833  103.8333  3/19/20    345
26679           Nepal            NaN  28.1667   84.2500  3/19/20      1
26680        Malaysia            NaN   2.5000  112.5000  3/19/20    900
...               ...            ...      ...       ...      ...    ...
27139  United Kingdom        Bermuda  32.3078  -64.7505  3/19/20      2
27140            Chad            NaN  15.4542   18.7322  3/19/20      1
27141     El Salvador            NaN  13.7942  -88.8965  3/19/20      1
27142            Fiji            NaN -17.7134  178.0650  3/19/20      1
27143       Nicaragua            NaN  12.8654  -85.2072  3/19/20      1

[276 rows x 6 columns]

In [64]:
fig1 = px.scatter_geo(data,
                     lat= 'Lat',
                     lon= 'Long',
                     hover_name="Country/Region", 
                     projection="natural earth",
                     hover_data=['cases'],    
                     title='Scatter Geo of Coronavirus on 19th March 2020')
fig1.show()

In [65]:
# fig1.write_image("scatter_geo.png")

### Density Heatmap

In [66]:
fig2 = px.density_mapbox(data,
                     lat = 'Lat',
                     lon= 'Long',
                     radius=10,
                     center=dict(lat=37, lon=-9),
                     zoom=0.8,
                     hover_name="Country/Region", # name to display when pass by mouse
                     hover_data=['cases','Province/State'],    
                     mapbox_style="carto-darkmatter",
                     title='World Heatmap of Coronavirus on 19th March 2020')
fig2.show()

In [13]:
!pip install psutil

In [15]:
#fig2.write_image("plotly-heatmap.png")

### Animation

Clean df by:
* Replacing 0 to NaN
* Remove all NaNs

In [117]:
df = pd.read_csv('time_series_2019-ncov-Confirmed.csv')

In [118]:
# We will need the dates to be in one column

df1 = pd.melt(df, id_vars=['Country/Region', 'Province/State','Lat','Long'])
df1.head()

Country/Region Province/State      Lat      Long variable  value
0       Thailand            NaN  15.0000  101.0000  1/22/20      2
1          Japan            NaN  36.0000  138.0000  1/22/20      2
2      Singapore            NaN   1.2833  103.8333  1/22/20      0
3          Nepal            NaN  28.1667   84.2500  1/22/20      0
4       Malaysia            NaN   2.5000  112.5000  1/22/20      0

In [119]:
df1 = df1.rename(columns={'variable':'date','value':'cases'})

In [120]:
df1.cases = df1.cases.replace(0,np.nan)
df1.cases

0        2.0
1        2.0
2        NaN
3        NaN
4        NaN
        ... 
27139    2.0
27140    1.0
27141    1.0
27142    1.0
27143    1.0
Name: cases, Length: 27144, dtype: float64

In [121]:
df1 = df1[df1.cases.notnull()]
df1

Country/Region Province/State      Lat      Long     date  cases
0            Thailand            NaN  15.0000  101.0000  1/22/20    2.0
1               Japan            NaN  36.0000  138.0000  1/22/20    2.0
154             China          Hubei  30.9756  112.2707  1/22/20  444.0
156      Korea, South            NaN  36.0000  128.0000  1/22/20    1.0
158             China      Guangdong  23.3417  113.4244  1/22/20   26.0
...               ...            ...      ...       ...      ...    ...
27139  United Kingdom        Bermuda  32.3078  -64.7505  3/19/20    2.0
27140            Chad            NaN  15.4542   18.7322  3/19/20    1.0
27141     El Salvador            NaN  13.7942  -88.8965  3/19/20    1.0
27142            Fiji            NaN -17.7134  178.0650  3/19/20    1.0
27143       Nicaragua            NaN  12.8654  -85.2072  3/19/20    1.0

[6703 rows x 6 columns]

In [106]:
fig2 = px.scatter_geo(df1,
                     lat= 'Lat',
                     lon= 'Long',
                     hover_name="Country/Region",
                     hover_data=['cases','Province/State'], 
                     animation_frame='date')
fig2.show()

---------------
## Choropleth Map

Drawing the map without China

In [155]:
no_china = df1[df1['Country/Region']!='China']

In [ ]:
fig3 = px.choropleth(no_china, 
                    locations="Country/Region", 
                    locationmode = "country names", #since you want world map
                    color='cases',
                    hover_name="Country/Region", 
                    animation_frame="date",
                    color_continuous_scale="Viridis",
                    )

fig3.show()